# Networking

## Linux networking

- Overview of network protocols and TCP/IP in Linux.
- Network configuration in Linux.
- Netplan on Ubuntu servers.
- Network settings in Red Hat for NetworkManager.
- Network troubleshooting tools: ping, traceroute, tcpdump.
- Network calculation with <TT>ipcalc</TT>
- Network applications and services.
- Network traffic sniffing with tcpdump.
- lighttpd server installation.
- Port tunneling with SSH.
<hr>

## Computers on the intertnet

- Network communication allows sending information, transfering files, and managing applications remotely between computers.
- Networks are organized in a series of layers implemented on each machine.
- The layers are independent and each layer offers a specific task to the neighboring layers above and below.
- The communication between the layers is based on defined rules and procedures, called protocols.
- Data is processed and passed through the layers from above to below, until the bottom layer is reached.
- At the bottom layer, computers communicate with each other via sending and receiving network datagrams through - cables, switches and routers.

![](img/computers_on_network.png)
<hr>

## TCP/IP 5 layer protocol suit


![](img/tcp-ip.jpg)

Each layer has its own task:


|TCP/IP Protocol Layer | Tasks
| :-- | :--
|5. Application Layer: ssh, ftp, http ... | Data segmentation by the application into Message Transfer Unit (MTU) segments. Typical MTU is 1.5 Kbyte, which includes the data payload plus 40 bytes for TCP and IP headers.
|4. Transport Layer: TCP, UDP, ports  | Connection management, quality, and ports to the applications
|3. Internet Layer: IP addresses, subnets, routing | Addressing: each computer has a unique address on its network or subnet. Routing between networks.
|2. Link Layer: Ethernet | Communication on the local network (subnet) through a switch. Media Access Card (MAC) address unique on the subnet. For example, 48:d2:4f:f4:d:fb, should be unique within a subnet. Address Resolution Protocol (ARP) matches the IP address to MAC on the subnet.
|1. Physical Layer: NIC, hubs, switches, routers, cabling, wifi APs and cards | Electronic devices to send and receive signals between computers.

<hr>

## OSI 7 layer Network Stack Model

![](img/osi.jpg)

|TCP/IP Protocol Layer | Task
| :-- | :--
|7. Application Layer: ssh, ftp, http ... | Data segmentation by the application into Message Transfer Unit (MTU) segments. Typical MTU is 1.5 Kbyte
|6. Presentation Layer: SSL, libz, XDR  | Data encryption, compression, and encoding/decoding
|5. Session Layer: Remote Procedure Call (RPC) | Responsible for opening, using and closing sessions. Remote procedures.

<hr>

## TCP/IP and Kernel

![](img/tcpip-kernel.jpg)

The Link, Internet and Transport layers are implemented through kernel.

<hr>

## Packet Encapsulation

Data is processed in form of packet encapsulation and transmitted/received in form of Ethernet frames.

![](img/ip_packet.jpg)

<hr>

## Hosts communication via TCP/IP

![](img/host-host.jpg)

![](img/host-tcpip.jpg)

<hr>

## Wired connection checkup (Exercise)

- To see whether your desktop is connected to a network switch and at what speed, use command  ```ethtool```.

- On your desktop, install package <TT>ethtool</TT>:
```bash
apt install ethtool
```
- See your network interfaces with command ```ifconfig``` or ```ip a```:
```bash
/sbin/ifconfig -a
```
or 
```bash
ip a
```

The main network interface, connected to the Ethernet, is <TT>enp0s3</TT>. Run command below:
```bash
/sbin/ethtool enp0s3
```

In the output, among various parameters, it doesn't show Speed and Duplex because the desktop is a VM in VDI.

  - Speed: Unknown!
  - Duplex: Unknown!
  - Link detected: yes
  
If the desktop was installed on a bare metal hardware, we would see something like below:

  - Speed: 1000Mb/s, 
  - Duplex: Full, 
  - Link detected: yes
  
Which means the cable is connected and the link speed is 1Gb/s speed, full duplex mode. 
  <hr>

## Network IP configuration

- Static configuration
    - IP address, gateway, hostname, and Domain Name System (DNS) are configured on the host.
    
    
    
- Dynamic Host Configuration Protocol (DHCP)
    - The settings are obtained from a DHCP server.
    
![](img/dhcp.gif)

<hr>

## Environment for IP configuration on Ubuntu and RedHat

|ifupdown scripts	| ```NetworkManager``` service 	| Netplan ```networkd``` service Meaning
|:---    | ---      | ---:        |  
|Old Debian/Ubuntu: | Ubuntu desktop, Debian, Redhat: | Ubuntu server: |
|File: ```/etc/network/interfaces``` |  Commands: ```nmtui, nmcli```     | File:```/etc/netplan/00-installer-config.yaml``` |
|RedHat:                 | Redhat                 | Command: ```netplan apply``` |
|File: ```/etc/sysconfig/network-scripts/ifcfg-ens3```|  File: ```/etc/NetworkManager/system-connections/<conn name>.nmconnection``` |
|Command:```ifup ens3``` |  ```systemctl restart NetworkManager; nmcli con up <conn name>```




<HR>



## Deploy a new VM for exercises

Shutdown <TT>kvm1</TT> VM, and clone it into <TT>netplan</TT> VM:
```bash
virsh shutdown kvm1
virt-clone  -o kvm1 -n netplan -f /home/hostadm/KVM/netplan.qcow2
```
Start netplan. Login to console of netplan:
```bash
virsh console netplan
```
Fix the hostname in file <TT>/etc/hostname</TT>.

Reset the machine ID by running the following script on netplan:
```bash
./vm_id_reset.sh
```

Execute command reboot on netplan:
```bash
reboot
```

<hr>


## Configuring network settings on Ubuntu server with Netplan (Exercises)

On <TT>netplan</TT> VM check the IP address settings by running command below:
```bash
ip addr
```
All the commands below in this section need to be run as root. Elevate the user privileges to root:
```bash
sudo -s
```

Assign IP address <TT>192.168.122.222</TT> by modifying the content of ```/etc/netplan/00-installer-config.yaml``` as follows:

```yaml
---
network:
  version: 2
  renderer: networkd
  ethernets:
    enp1s0:
      dhcp4: false
      addresses:
        - 192.168.122.222/24
      routes:
        - to: default
          via: 192.168.122.1
      nameservers:
        addresses: [192.168.122.1]
```

Install the Yaml syntax check tool:
```bash
apt install yamllint
```

Check the network configuration file for syntax correctness:
```bash
yamllint /etc/netplan/00-installer-config.yaml
```
If no errors found, have the new network settings applied:
```bash
netplan apply
```
Check the IP address again:
```bash
ip addr
```
It should show <TT>192.168.122.222</TT> for <TT>ens3</TT> interface now.

See the gateway settings by running command 
```bash
ip route show
```
It should show the "default via 192.168.122.1"

Logout and disconnect from the console.
<hr>

## Clone rocky9 VM (Exercises)

In case you already have ```rocky91``` VM from the package management class, skip the cloning steps below and proceed to the 
 network configuration on ```rocky91```.
 
Make sure rocky9 is down:
```bash
virsh list
virsh stop rocky9
```
Clone rocky9 into new VM rocky91:
```bash
virt-clone -o rocky9 -n rocky91 -f /home/hostadm/KVM/rocky91.qcow2
```
Start the VM:
```bash
virsh start rocky91
```
Connect to the cnsole:
```bash
virsh console rocky91
```
Login to the system.

You need to install editor `dbus-tools`:
```bash
sudo dnf install dbus-tools
```

Change the hostname to `rocky91` by editing file `/etc/hostname` with `nano`.

Reset the machine ID:
```bash
sudo dnf install dbus-tools
sudo rm -f /etc/machine-id
sudo dbus-uuidgen --ensure=/etc/machine-id
sudo dbus-uuidgen --ensure
sudo dhclient -r eth0
```

Reboot the VM.

<hr>

## Network configurations on a Red Hat server (Exercises)

On RedHat based systems, we can use ```nmcli``` to control the network settings in the NetworkManager service.

Start rocky91 VMs:
```bash
virsh start rocky91
```
Login to console of rocky91:
```bash
virsh console rocky91
```
Execute command ip address show to read the IP address:
```bash
ip addr show eth0
```
Try pinging ```netplan``` by its IP address, for example:
```bash
ping -c 3 192.168.122.222
```
Become root on rocky91 VM
```bash
sudo -s
```

By using command ```nmcli``` check available and active connactions:
```bash
nmcli conn show
```
There is connection named "System eth0" for interface eth0.

See the settings for device eth0:
```bash
nmcli dev show eth0
```

With command ```nmcli```, we can create various connections with different settings for eth0 interface, then we can activate the needed connection, and de-activate non-needed.

Let's create new connection named "eth_static" and assign it static IP address 192.168.122.126 and netmask /24:
```bash
nmcli con add type ethernet con-name eth_static ip4 192.168.122.126/24 gw4 192.168.122.1 ipv4.dns 192.168.122.1
```
Activate the connection:
```bash
nmcli con up eth_static
```
Check the connection status:
```bash
nmcli conn show
```
Check the new IP address:
```bash
ip addr show eth0
```

Change the IP address to 192.168.122.25 via ```nmcli``` command:
```bash
nmcli con modify eth_static ipv4.addresses 192.168.122.125/24
```
Activate eth_static connection:
Activate the connection:
```bash
nmcli con up eth_static
```
Check the connection status:
```bash
nmcli conn show
```
Check the new IP address:
```bash
ip addr show eth0
```

**Alternative way of modifying the IP address settings for a connection.**

When creating a new connection with ```nmcli``` command, a new file is created in directory 
 /etc/NetworkManager/system-connections/.

We can modify the settings in the file with an editor, then restart the NetworkManager and activate the connection, for example:
```bash
systemctl restart NetworkManager
nmcli con up eth_static
```

**Revert back to the DHCP based connection**

```bash
nmcli conn show
```

We need to activate connection "System eth0":
```bash
nmcli conn up "System eth0"
```
<hr>

## Internet Control Message Protocol (ICMP) protocol (Exercises)

Implemented on hosts and gateways (routers) for:

Reporting the status of datagram processing.
Diagnostics of connection and routing.
Reporting errors in the processing of a datagram.

Example: ```ping```

![](img/ping.jpg)

Exercise: command ```ping```.
```bash
ping -c 5 capone.rutgers.edu
ping -c 5 engsoft.rutgers.edu
ping -c 5 google.com
```
If the systems respond, it means they are reachable on the network. Notice how varies the round-trip time and Time to Live (ttl) for packets between the hosts.

Example: ```traceroute```


![](img/traceroute.jpg)

Time to leave (TTL) decrement. The TTL value of an IP packet represents the maximum number of IP routers that the packet can go through before being thrown away. You can expect each router in the Internet to decrement the TTL field by exactly one. The default TTL for traceroute on Linux is 30. It can be increased up to 255 maximum by using the -m command option.

Exercise: command traceroute.

```bash
sudo apt install traceroute
sudo /usr/sbin/traceroute -I capone.rutgers.edu
sudo /usr/sbin/traceroute -I engsoft.rutgers.edu
sudo /usr/sbin/traceroute -I google.com
```
This shows you all the gateways between the subnets your packet travels towards the destination. Notice the difference in the number of gateways between your desktop and the three remote hosts as well as the round trip times.

<hr>

## Subnets and routing

Example: Host A can communicate with both the hosts - B and C. Hosts B and C can't communicate with each other.
What is the problem?
<br>
Answer: the routing (gateway) is not defined on Host B.

![](img/hosts-router.png)

## Network calculation, gateway and routing

- Computers connected to the same switch are on the same network/subnet and communicate with each other directly through the switch.
- For computers located on the different networks/subnets, gateway/router is needed.
- To define the local subnet, netmask is used.

- Subnet mask defines the network and the host parts of the IP address

Network address = Host address (logical AND) Netmask:



| Address         | Decimal/Hexadecimal  | Binary | 
|:- | :-: | :- |                                  
| IP address      | 192.168.5.10  |  ```11000000 10010100 00000101 00001010``` |  
| Netmask         | 255.255.255.0 |  ```11111111 11111111 11111111 00000000``` |
| Network address | 192.168.5.0   |  ```11000000 10010100 00000101 00000000``` |



- The network address is the smallest address on the network:

```11000000 10010100 00000101 00000000 = 192.168.5.0```

- The broadcast address is the largest address on the network:

```11000000 10010100 00000101 11111111 = 192.168.5.255```

- Max number of hosts on the subnet: 254 = 256 - 2
The gateway address should be on the same subnet with the host

- Subnet mask consists of contiguous 1. The bytes filled with 1 become 255 in decimal notation.  The bytes ending with 0 can be converted from binary to decimal by the following technique:
  
  $a_7 \cdot 128 + a_6 \cdot 64 + a_5 \cdot 32 + a_4 \cdot 16 + a_3 \cdot 8 + a_2 \cdot 4 + a_1 \cdot 2 + a_0$

  where the coefficients, $a_7, a_6, a_5, a_4, a_3, a_2, a_1, a_0$, are the bits with values of 0 or 1.

- It is easier to use ipcalculator for computing subnets.
<hr>


## IP calculator exercises

Network IP calculations with ipcalc
On the desktop, install ipcalc by using APT:
```bash
apt install ipcalc
```
Run ipcalc for network address 192.168.5.0 with subnet mask 255.255.255.0.
```bash
ipcalc 192.168.5.0/255.255.255.0
```
See the output for Address, Netmask, Network, HostMin, HostMax, Broadcast, Hosts/Net.
Notice the same results for the same network and the different representation of the netmask:
```bash
ipcalc 192.168.5.0/24
```
Notice the same results for Netmask, Network, HostMin, HostMax, Broadcast, Hosts/Net if using the different IP addresses within the same network in ipcalc, for example:
```bash
ipcalc 192.168.5.15/24
ipcalc 192.168.5.34/24
```
Run ipcalc for subnets (networks) 192.168.5.0/25 and 192.168.5.128/25:
```bash
ipcalc 192.168.5.0/25
ipcalc 192.168.5.128/25
```
Notice the values for HostMin and HostMax in both the cases. By looking at the ranges [HostMin, HostMax], you can see, for example, that IP address 192.168.5.5 belongs to the first subnet and 192.168.5.250 to the second.
You can verify that by running ipcalc on the IP addresses above and then comparing the Network values:
```bash
ipcalc 192.168.5.5/25
ipcalc 192.168.5.250/25
```

<hr>

## Network applications: ssh, sftp, scp, rsync (Exercises)

Make sure virtual machine netplan is running
```bash
virsh list
```
Figure out the IP address of netplan:
```bash
virsh domifaddr netplan
```

Place the IP address and netplan host name into file ```/etc/hosts``` on your desktop. 
netplan  IP is 192.168.122.222
```bash
nano /etc/hosts
```
Make entry in the file:  ```192.168.122.222   netplan```

ssh to netplan as user hostadm:
```bash
ssh hostadm@netplan
```

Configure SSH for private/public key authentication.
For SSH authentication, you can use either RSA or DSA public/private keys besides password. We'll be using RSA in the exercises below.
To generate an RSA key pair, type the following command at a shell prompt on your desktop:
```bash
ssh-keygen -t rsa
```
Accept the default file location of ```~/.ssh/id_rsa```. Enter a passphrase different from your account password and confirm it by entering it again.
The public key is written to ```~/.ssh/id_rsa.pub```. The private key is written to ```~/.ssh/id_rsa```.
Never distribute your private key to anyone.
The contents of ```~/.ssh/id_rsa.pub``` needs to be delivered onto the remote machine to which you want to connect, specifically netplan, into file ```~/.ssh/authorized_keys```
To accomplish the transfer task, here you can use one of the commands for file transfer.
Commands ```scp``` and ```sftp``` come with ssh. We use interactive ```sftp``` command here:
```bash
sftp  netplan
Name (netplan:hostadm): hostadm
sftp> cd .ssh
sftp> lcd .ssh
sftp> put id_rsa.pub authorized_keys
sftp>  quit
```
Command ```cd``` in the sftp> shell above is for stepping into the directory, .ssh, on the remote host, netplan.
Command ```lcd``` is for stepping into the directory, .ssh, on the local desktop.

Now try to ssh to netplan. You should be prompted to enter your passphrase.

The ```ssh-agent``` can be used to store your passphrase so that you do not have to enter it each time you make a ssh or scp connection.
At a shell prompt on the desktop, type the following command:
```bash
exec ssh-agent $SHELL
```
Then type the command:
```bash
ssh-add
```
and enter your passphrase(s). If you have more than one key pair configured, you will be prompted for each one. When you log out, your passphrase(s) will be forgotten. You must execute these two commands each time you log in to a virtual console or open a terminal window.

Run a remote command over ssh, for example:
```bash
ssh netplan "uname -a"
```
Beside ```sftp```, command ```scp``` can be used for copying files from host to host.
In `scp`, the first argument is the <i>source_host:source_file</i>, the second is <i>destination_host:destination_dir</i>. If the source_host or the destination_host is local, it is absent in the argumernt. The local directory is signified by ```.```

Copy file /etc/hosts from netplan VM to the current directory on the desktop by using scp command:
```bash
scp netplan:/etc/hosts .
```

Copy new file, somef.txt, from the local directory to the home directory on netplan VM.
```bash
touch somef.txt
scp somef.txt netplan:/home/$USER
```

You can also copy a group of files, for example, somef.txt and /etc/hosts, by placing them in block {}:
```bash
scp {somef.txt,/etc/hosts} netplan:/home/$USER
```

Directories can be copied recursively with ```scp```. For example, to copy /etc directory recursively from the desktop to  the user home directory on netplan:
```bash
scp -r /etc netplan:
```

Syncronizing directories between remote hosts by using ```rsync```.
This tool lets you copy files and directories between a local host and a remote host.
Install ```rsync``` on both your desktop and netplan:
```bash
apt install rsync
```
Creat a directory tree and copy it over to netplan with rsync command.
```bash
mkdir -p dir1/dir2/dir3
rsync  -avz dir1 netplan:/home/$USER
```
Option a stands for archive (preserve links and timestamps); <TT>v</TT> is for verbose and <TT>z</TT> is for data compression when sending-receiving.

<hr>

## Send/receive data with netcat (Exercises)

Netcat is a very useful tool to connect to any TCP and UDP port on a remote host, and send/receive data.


Start both, netplan and rocky91 VMs:
```bash
virsh start netplan
virsh start rocky91
```
Start ```tmux``` on your desktop, and split the terminal into two panes.

In one pane, login to console of netplan:
```bash
virsh console netplan
```
In the other pane of tmux, login to rocky91:
```bash
virsh console rocky91
```

Become root on both the VMs
```bash
sudo -s
```

| Step | On Ubuntu (server) | On rocky91 |
|:- | :-: | -: |     
|1.  |Install netcat: ```apt install netcat``` | ```dnf install nmap-ncat``` | 
|2.    | Start netcat as a server, listening on port UDP/8080: |  Connect to UDP/8080 port on netplan, 192.168.122.222: |  
|      | ```netcat -l -u 8080``` | ```ncat 192.168.122.222 -u 8080``` | 
|3.    | When the session is over, type Ctrl-C to stop the netcat server.  |     Start typing text. Hit ENTER key. The text should appear on the both terminals. Press Ctrl+D to close the UDP connection. | 
|4.    | Start the server on TCP/8080 to write into a file, outputfile.txt |   Send file /etc/hosts to TCP/8080 on netplan VM via netcat |
|   | ```netcat -l 8080 > outputfile.txt```  |  ```ncat 192.168.122.222  8080 < /etc/hosts``` | 
|5.  |  After the file is received, the connection closes itself. Check the content of the file: |  |
|    | ```less outputfile.txt```  |  
|6.  | Start ```netcat``` to receive a directory via ```tar``` command:   | Send ```/etc``` directory via ```tar``` and netcat: | 
|    | ```netcat -l 8080 \| tar xf -```   |  ```tar cf - /etc \| nc -w 20  192.168.122.222  8080``` |
|7.  | Check if the directory tree has been transferred:  | |
|    |  ```tree etc``` | |
 

`netcat` provides away faster transfer of files and directories than `scp`, but it can be used only on a private network.
<hr>

## tcpdump command to see the traffic on NIC (Exercises)

When you need to see all the network traffic on a network card, you can run the command for the network interface.
It helps to identify the subnet your system is connected to, and see all the active traffic.

On netplan VM, install tcpdump:
```bash
apt install tcpdump
```
Run command `tcpdump` on the ethernet interface:
```bash
tcpdump -v -n -i enp1s0
```

On rocky91 VM, start pingin the IP address of netplan VM:
```bash
ping 192.168.122.222
```

See the output in tcpdump on netplan VM.
It should show some traffic related to echo request and reply from rocky VM:

```
    192.168.122.126 > 192.168.122.222: ICMP echo request ...
    192.168.122.222 > 192.168.122.126: ICMP echo reply ...
```

```tcpdum``` is very noisy because it picks up all the packets going through interface enp1s0.
We can filter the output by the IP, protocol, and port, for example:
```bash
tcpdump -v -n -i enp1s0 host 192.168.122.126 and proto \\icmp
```
The IP address of rocky91 is 192.168.122.126 here. In your case it maybe different.

To see only the incoming packets, use the `src` IP address:
```bash
tcpdump -v -n -i enp1s0 src host 192.168.122.126 and proto \\icmp
```

Move to the pane with rocky91 in ```tmux```.

SSH to netplan and start ```tcpdump``` with reading the traffic, coming from rocky91, on local port udp/8080:
```bash
sudo tcpdump -i enp1s0 src host 192.168.122.126 and dst port 8080 -A
```

<hr>

## Light web server, lighttpd, for file download (Exercises)

- On netplan VM, install lighttpd:
```bash
apt install lighttpd
```

Add the following line to the server configuration file, ```/etc/lighttpd/lighttpd.conf```, right after the line with 
```server.port = 80```:
```{admonition} add to lighttpd.conf 
    dir-listing.activate   = "enable"
```
Restart the service:
```bash
systemctl restart lighttpd
```
Populate files and directories in the server document-root directory, ```/var/www/html```:
```bash
cd /var/www/html
apt download lua5.4
dpkg -X lua5.4_5.4.4-1_amd64.deb LUA
```
Remove the index file from the directory:
```bash
rm index.lighttpd.html
```

- On the desktop, create new directory DOWNLOADS, then download file lua5.4_5.4.4-1_amd64.deb from the web server into the directory:
```bash
mkdir DOWNLOADS
cd DOWNLOADS
wget http://192.168.122.222/lua5.4_5.4.4-1_amd64.deb
```

Download the whole directory recursively:
```bash
wget --recursive -nH http://192.168.122.222/
```

***

## SSH local port tunneling (Exercise).

With SSH you can make a tcp port available from a private network to your local system.
For example, we can map port tcp/80 from 192.168.122.222 to your localhost:8080 via SSH to the desktop.

Add the port mapping option to the SSH command you usually use:
```{admonition} add this to your ssh command you run to the desktop
    -L 8080:192.168.122.222:80
```

In the browser on your laptop, navigate to port 8080 at localhost:
```{admonition} in the browser
http://localhost:8080/
```

***